In [20]:
import pennylane as qml
from pennylane import numpy as np
import tensorflow as tf
from tensorflow.keras import datasets, layers, models
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.layers import Dense
import time

import pennylane as qml
from pennylane import numpy as np
import tensorflow as tf
from tensorflow.keras.datasets import cifar10
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import StandardScaler
import time

In [21]:
# Parameters
n_qubits = 4  # Number of qubits in the quantum circuit
n_classes = 10  # Number of CIFAR-10 classes

# Define quantum device
dev = qml.device("default.qubit", wires=n_qubits)

# Quantum circuit layer
def quantum_circuit(inputs, weights):
    qml.templates.AngleEmbedding(inputs, wires=range(n_qubits))
    qml.templates.BasicEntanglerLayers(weights, wires=range(n_qubits))
    # Ensure outputs are real numbers
    return [qml.expval(qml.PauliZ(i)) for i in range(n_qubits)]

# Wrap quantum_circuit as a QNode
qnode = qml.QNode(quantum_circuit, dev, interface="tf")

# Quantum layer in Keras
weight_shapes = {"weights": (2, n_qubits)}  # 2 layers, n_qubits parameters per layer
qlayer = qml.qnn.KerasLayer(qnode, weight_shapes, output_dim=n_qubits, dtype="float32")


In [22]:
# Load CIFAR-10 dataset
(x_train, y_train), (x_test, y_test) = cifar10.load_data()

# Preprocessing
# Normalize pixel values
x_train = x_train.astype("float32") / 255.0
x_test = x_test.astype("float32") / 255.0

# Flatten images and downsample to match quantum input size
x_train = x_train.reshape((x_train.shape[0], -1))[:, :n_qubits]
x_test = x_test.reshape((x_test.shape[0], -1))[:, :n_qubits]

# Scale features
scaler = StandardScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.transform(x_test)

# Convert labels to one-hot encoding
y_train = to_categorical(y_train, n_classes)
y_test = to_categorical(y_test, n_classes)

In [24]:
# Define the hybrid model
model = tf.keras.Sequential([
    tf.keras.layers.Input(shape=(n_qubits,), dtype="float32"),
    qlayer,
    tf.keras.layers.Dense(n_classes, activation="softmax", dtype="float32")
])

# Compile the model
model.compile(optimizer="adam", loss="categorical_crossentropy", metrics=["accuracy"])

# Train and evaluate the model
# Benchmark training time
start_train_time = time.time()
history = model.fit(x_train, y_train, epochs=3, batch_size=64, validation_data=(x_test, y_test))
end_train_time = time.time()

# Benchmark prediction time
start_pred_time = time.time()
test_loss, test_acc = model.evaluate(x_test, y_test, verbose=2)
end_pred_time = time.time()

# Calculate and print benchmark results
train_time = end_train_time - start_train_time
pred_time = end_pred_time - start_pred_time

print("\nTraining time: {:.2f} seconds".format(train_time))
print("Prediction (evaluation) time: {:.2f} seconds".format(pred_time))
print("Test accuracy:", test_acc)

Epoch 1/3
782/782 [==============================] - 229s 293ms/step - loss: 2.2458 - accuracy: 0.1437 - val_loss: 2.2007 - val_accuracy: 0.1729
Epoch 2/3
782/782 [==============================] - 212s 271ms/step - loss: 2.1943 - accuracy: 0.1768 - val_loss: 2.1758 - val_accuracy: 0.1820
Epoch 3/3
782/782 [==============================] - 155s 198ms/step - loss: 2.1792 - accuracy: 0.1781 - val_loss: 2.1641 - val_accuracy: 0.1806
313/313 - 22s - loss: 2.1641 - accuracy: 0.1806 - 22s/epoch - 71ms/step

Training time: 595.97 seconds
Prediction (evaluation) time: 22.31 seconds
Test accuracy: 0.18060000240802765
